In [1]:
!pip install "u8darts[all]"
!pip install optuna
!pip install ta

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 819.6/819.6 kB 6.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 12.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 160.5/160.5 kB 16.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 535.7/535.7 kB 14.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 120.7/120.7 kB 12.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.0/44.0 kB 3.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 776.9/776.9 kB 18.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.7/101.7 kB 10.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 98.5/98.5 MB 7.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 840.4/840.4 kB 21.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 279.8/279.8 kB 22.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.1/61.1 k

In [2]:
import ta
from sklearn.ensemble import RandomForestRegressor
from darts import TimeSeries
from datetime import datetime
from darts.dataprocessing.transformers import Scaler
from darts import concatenate
from darts.utils.timeseries_generation import datetime_attribute_timeseries as dt_attr
from darts.models import RNNModel, AutoARIMA, NaiveDrift, CatBoostModel, NaiveSeasonal, ExponentialSmoothing, Prophet, BATS, TBATS
import matplotlib.pyplot as plt
import numpy as np
from darts.utils.callbacks import TFMProgressBar
import torch
import plotly.graph_objects as go
from darts.metrics import mae, rmse, mse, mape




torch.manual_seed(1)
np.random.seed(1)

In [3]:
#actual: actual series
#prediction: predicted series
#print_single can be [True, False]. If True print one prediction associated to 1 model
#otherwise a list of predictions associated to different models
def print_graph_backtesting(actual, prediction, print_single, model, horizon):
    fig = go.Figure()


    fig.add_trace(go.Scatter(x=actual.time_index,
                             y=actual.values().flatten(),
                             name='Real test points'))

    if print_single:
        fig.add_trace(go.Scatter(x=prediction.time_index,
                                 y=prediction.values().flatten(),
                                 name=f'Predicted points ({model})',
                                ))
    else:
        for key, pre in prediction.items():
            fig.add_trace(go.Scatter(x=pre.time_index,
                                     y=pre.values().flatten(),
                                     name=f'Predicted points ({key})',
                                    ))

    fig.update_layout(title_text = f"Backtesting for Bitcoin prices with Forecasting Horizon = {horizon}")
    fig.update_xaxes(title_text="Date")
    fig.update_yaxes(title_text="Price")
    fig.show()

#Collect Bitcoin data

In [4]:
dates = ['2013-04-01', '2016-07-19', '2017-04-01', '2019-12-31']
data_sets = []

In [5]:
import requests
import pandas as pd
from datetime import datetime

def fetch_crypto_compare_data(symbol, comparison_symbol, limit, to_timestamp):
    url = 'https://min-api.cryptocompare.com/data/v2/histoday'
    params = {
        'fsym': symbol,
        'tsym': comparison_symbol,
        'limit': limit,
        'toTs': to_timestamp
    }
    response = requests.get(url, params=params)
    data = response.json()['Data']['Data']
    return data

def get_crypto_compare_ohlcv(symbol, comparison_symbol, start_date, end_date):
    df = pd.DataFrame()
    current_date = end_date

    while current_date > start_date:
        data = fetch_crypto_compare_data(symbol, comparison_symbol, 2000, int(current_date.timestamp()))
        current_date = datetime.fromtimestamp(data[0]['time'])
        df = pd.concat([pd.DataFrame(data), df], ignore_index=True)

    df['time'] = pd.to_datetime(df['time'], unit='s')
    df = df[(df['time'] >= start_date) & (df['time'] <= end_date)]
    return df

In [6]:
data_sets = []

In [7]:
date_format = "%Y-%m-%d"

for i in range(len(dates) - 1):
  start_date = datetime.strptime(dates[0], date_format)
  end_date = datetime.strptime(dates[i + 1], date_format)
  df = get_crypto_compare_ohlcv('BTC', 'USD', start_date, end_date)
  df['time'] = pd.to_datetime(df['time'])
  df.set_index('time', inplace=True)
  print(pd.infer_freq(df.index))
  del df['conversionType']
  del df['conversionSymbol']
  df = ta.utils.dropna(df)
  df = ta.add_all_ta_features(
    df, "open", "high", "low", "close", "volumeto", fillna=True
  )
  df = df.fillna(0)
  data_sets.append(df)

D
D
None


In [8]:
data_sets[2] = data_sets[2][~data_sets[2].index.duplicated(keep='first')]
print(pd.infer_freq(data_sets[2].index))

D


# Feature engineering

In [9]:
past_covs = []
past_covs_scaled = []
future_covs_scaled = []
targets = []
trains_scaled = []
tests_scaled = []
targets_scaled = []
tests = []
scalers = []

In [10]:
for d in data_sets:
  split_index = int(len(d) * 0.8)  # 80% for training, 20% for testing
  X_train = d.iloc[:split_index].drop('close', axis=1)
  y_train = d.iloc[:split_index]['close']
  X_test = d.iloc[split_index:].drop('close', axis=1)
  y_test = d.iloc[split_index:]['close']
  clf = RandomForestRegressor(n_jobs=-1)
  clf.fit(X_train, y_train)
  clf.score(X_test, y_test)
  features = {k: v for k, v in sorted(zip(X_train.columns, clf.feature_importances_), key=lambda x: x[1], reverse=True)}
  filtered_features = {feature: importance for feature, importance in features.items() if importance >= 0.01}
  filtered_features
  filtered_feature_names = list(filtered_features.keys())
  d = d.reset_index()
  covs = TimeSeries.from_dataframe(d, time_col="time", value_cols=filtered_feature_names)
  covs = covs.astype(np.float32)
  past_covs.append(covs)
  target = TimeSeries.from_dataframe(d, time_col="time", value_cols=["close"])
  target = target.astype(np.float32)
  targets.append(target)


# Create Train, Validation and Test Set + Past and Future Covariates

In [11]:
#create train and test series and scale them
for t in targets:

  split_index = int(len(t) * 0.8)
  train_target = t[:split_index]

  test_target = t[split_index:]

  tests.append(test_target)

  scaler_target = Scaler()

  scalers.append(scaler_target)

  scaler_target = scaler_target.fit(train_target)


  train_scaled = scaler_target.transform(train_target)
  test_scaled = scaler_target.transform(test_target)
  target_scaled = concatenate([train_scaled, test_scaled])

  trains_scaled.append(train_scaled)
  tests_scaled.append(test_scaled)
  targets_scaled.append(target_scaled)

  past_cov = concatenate(
    [
        dt_attr(t.time_index, "month", dtype=np.float32),
        dt_attr(t.time_index, "year", dtype=np.float32),
        dt_attr(t.time_index, "day", dtype=np.float32),
        dt_attr(t.time_index, "dayofweek", dtype=np.float32),
        dt_attr(t.time_index, "week", dtype=np.float32),
        dt_attr(t.time_index, "dayofyear", dtype=np.float32),
        past_covs[targets.index(t)],
    ],
    axis="component",
  )


  scaler_ft_past = Scaler()

  past_cov = scaler_ft_past.fit_transform(past_cov)
  past_covs_scaled.append(past_cov)

  future_cov = concatenate(
    [
        dt_attr(t.time_index, "month", dtype=np.float32),
        dt_attr(t.time_index, "year", dtype=np.float32),
        dt_attr(t.time_index, "day", dtype=np.float32),
        dt_attr(t.time_index, "dayofweek", dtype=np.float32),
        dt_attr(t.time_index, "week", dtype=np.float32),
        dt_attr(t.time_index, "dayofyear", dtype=np.float32),
    ],
    axis="component",
  )

  scaler_ft_future = Scaler()

  future_cov = scaler_ft_future.fit_transform(future_cov)
  future_covs_scaled.append(future_cov)

# Create csv file where to store all of the Error Metrics

In [12]:
import csv

headers = ['Model', 'MAE', 'RMSE', 'MSE', 'MAPE']
separator = ['-', '-', '-', '-', '-']

with open('error_metrics.csv', 'w', newline='') as file:
    writer = csv.writer(file)

    # Write the header
    writer.writerow(headers)

def add_row(row):
  with open('error_metrics.csv', 'a', newline='') as file:
    writer = csv.writer(file)
    writer.writerow(row)

# Naive + Naive Seasonal + Naive Drift

In [13]:
naive_drift_model = NaiveDrift()
naive_model = NaiveSeasonal()
naive_seasonal_model = NaiveSeasonal(7)

# Backtesting Naive Drift Model

In [14]:
bt_horizons = [1, 7 , 30, 90]
from datetime import timedelta

In [28]:
backtesting_Drift = [[], [], []]
backtesting_Naive = [[], [], []]
backtesting_NaiveSeasonal = [[], [], []]

In [16]:
for t in targets_scaled:
  for h in bt_horizons:
    hist_Drift = naive_drift_model.historical_forecasts(
            t,
            start=tests_scaled[targets_scaled.index(t)].time_index[0] - timedelta(days=h),
            forecast_horizon=h,
            stride=1,
            verbose=True,
      )
    hist_predict_Drift = scalers[targets_scaled.index(t)].inverse_transform(hist_Drift)
    backtesting_Drift[targets_scaled.index(t)].append(hist_predict_Drift)

100%|██████████| 495/495 [00:02<00:00, 230.68it/s]


In [17]:
for i in range(3):
  for b in backtesting_Drift[i]:
    h = bt_horizons[backtesting_Drift[i].index(b)]
    print_graph_backtesting(tests[i], b, True, 'naive_drift_model',h)

In [18]:
add_row(['Backtesting Naive Drift Model','','','',''])
for i in range(3):
  add_row([f'time period = {i + 1}', '', '', '', ''])
  for b in backtesting_Drift[i]:
    print(f"MAE of Naive Drift Model forecasting horizon = {bt_horizons[backtesting_Drift[i].index(b)]}: {mae(tests[i], b)}")
    print(f"RMSE of Naive Drift Model forecasting horizon = {bt_horizons[backtesting_Drift[i].index(b)]}: {rmse(tests[i], b)}")
    print(f"MSE of Naive Drift Model forecasting horizon = {bt_horizons[backtesting_Drift[i].index(b)]}: {mse(tests[i], b)}")
    print(f"MAPE of Naive Drift Model forecasting horizon = {bt_horizons[backtesting_Drift[i].index(b)]}: {mape(tests[i], b)}")
    print("\n")
    row = [f'Naive Drift fh={bt_horizons[backtesting_Drift[i].index(b)]}', mae(tests[i], b), rmse(tests[i], b), mse(tests[i], b), mape(tests[i], b) ]
    add_row(row)

MAE of Naive Drift Model forecasting horizon = 1: 8.886646270751953
RMSE of Naive Drift Model forecasting horizon = 1: 15.339116096496582
MSE of Naive Drift Model forecasting horizon = 1: 235.28848266601562
MAPE of Naive Drift Model forecasting horizon = 1: 1.7981471493840218


MAE of Naive Drift Model forecasting horizon = 7: 25.665679931640625
RMSE of Naive Drift Model forecasting horizon = 7: 40.46351623535156
MSE of Naive Drift Model forecasting horizon = 7: 1637.2962646484375
MAPE of Naive Drift Model forecasting horizon = 7: 5.129487067461014


MAE of Naive Drift Model forecasting horizon = 30: 58.20355224609375
RMSE of Naive Drift Model forecasting horizon = 30: 81.96307373046875
MSE of Naive Drift Model forecasting horizon = 30: 6717.94580078125
MAPE of Naive Drift Model forecasting horizon = 30: 11.593835800886154


MAE of Naive Drift Model forecasting horizon = 90: 106.03575134277344
RMSE of Naive Drift Model forecasting horizon = 90: 131.37071228027344
MSE of Naive Drift Mod

# Backtesting Naive Model

In [19]:
for t in targets_scaled:
  for h in bt_horizons:
    hist_Naive = naive_model.historical_forecasts(
            t,
            start=tests_scaled[targets_scaled.index(t)].time_index[0],
            forecast_horizon=h,
            stride=1,
            verbose=True,
      )
    hist_predict_Naive = scalers[targets_scaled.index(t)].inverse_transform(hist_Naive)
    backtesting_Naive[targets_scaled.index(t)].append(hist_predict_Naive)

100%|██████████| 405/405 [00:01<00:00, 250.17it/s]


In [20]:
for i in range(3):
  for b in backtesting_Naive[i]:
    h = bt_horizons[backtesting_Naive[i].index(b)]
    print_graph_backtesting(tests[i], b, True, 'naive_model',h)

In [21]:
add_row(['Backtesting Naive Model','','','',''])
for i in range(3):
  add_row([f'time period = {i + 1}', '', '', '', ''])
  for b in backtesting_Naive[i]:
    print(f"MAE of Naive Model forecasting horizon = {bt_horizons[backtesting_Naive[i].index(b)]}: {mae(tests[i], b)}")
    print(f"RMSE of Naive Model forecasting horizon = {bt_horizons[backtesting_Naive[i].index(b)]}: {rmse(tests[i], b)}")
    print(f"MSE of Naive Model forecasting horizon = {bt_horizons[backtesting_Naive[i].index(b)]}: {mse(tests[i], b)}")
    print(f"MAPE of Naive Model forecasting horizon = {bt_horizons[backtesting_Naive[i].index(b)]}: {mape(tests[i], b)}")
    print("\n")
    row = [f'Naive fh={bt_horizons[backtesting_Naive[i].index(b)]}', mae(tests[i], b), rmse(tests[i], b), mse(tests[i], b), mape(tests[i], b) ]
    add_row(row)

MAE of Naive Model forecasting horizon = 1: 8.935952186584473
RMSE of Naive Model forecasting horizon = 1: 15.361613273620605
MSE of Naive Model forecasting horizon = 1: 235.9791717529297
MAPE of Naive Model forecasting horizon = 1: 1.8083993345499039


MAE of Naive Model forecasting horizon = 7: 26.396310806274414
RMSE of Naive Model forecasting horizon = 7: 41.312774658203125
MSE of Naive Model forecasting horizon = 7: 1706.7452392578125
MAPE of Naive Model forecasting horizon = 7: 5.238295346498489


MAE of Naive Model forecasting horizon = 30: 60.804649353027344
RMSE of Naive Model forecasting horizon = 30: 86.37228393554688
MSE of Naive Model forecasting horizon = 30: 7460.171875
MAPE of Naive Model forecasting horizon = 30: 11.679375916719437


MAE of Naive Model forecasting horizon = 90: 105.4735336303711
RMSE of Naive Model forecasting horizon = 90: 141.77847290039062
MSE of Naive Model forecasting horizon = 90: 20101.134765625
MAPE of Naive Model forecasting horizon = 90: 18.3

# Backtesting Naive Seasonal Model

In [29]:
for t in targets_scaled:
  for h in bt_horizons:
    hist_NaiveSeasonal = naive_seasonal_model.historical_forecasts(
            t,
            start=tests_scaled[targets_scaled.index(t)].time_index[0],
            forecast_horizon=h,
            stride=1,
            verbose=True,
      )
    hist_predict_NaiveSeasonal = scalers[targets_scaled.index(t)].inverse_transform(hist_NaiveSeasonal)
    backtesting_NaiveSeasonal[targets_scaled.index(t)].append(hist_predict_NaiveSeasonal)

100%|██████████| 405/405 [00:01<00:00, 244.62it/s]


In [30]:
for i in range(3):
  for b in backtesting_NaiveSeasonal[i]:
    h = bt_horizons[backtesting_NaiveSeasonal[i].index(b)]
    print_graph_backtesting(tests[i], b, True, 'naive_seasonal_model',h)

In [31]:
add_row(['Backtesting Naive Seasonal Model','','','',''])
for i in range(3):
  add_row([f'time period = {i + 1}', '', '', '', ''])
  for b in backtesting_NaiveSeasonal[i]:
    print(f"MAE of Naive Seasonal Model forecasting horizon = {bt_horizons[backtesting_NaiveSeasonal[i].index(b)]}: {mae(tests[i], b)}")
    print(f"RMSE of Naive Seasonal Model forecasting horizon = {bt_horizons[backtesting_NaiveSeasonal[i].index(b)]}: {rmse(tests[i], b)}")
    print(f"MSE of Naive Seasonal Model forecasting horizon = {bt_horizons[backtesting_NaiveSeasonal[i].index(b)]}: {mse(tests[i], b)}")
    print(f"MAPE of Naive Seasonal Model forecasting horizon = {bt_horizons[backtesting_NaiveSeasonal[i].index(b)]}: {mape(tests[i], b)}")
    print("\n")
    row = [f'Naive Seasonal fh={bt_horizons[backtesting_NaiveSeasonal[i].index(b)]}', mae(tests[i], b), rmse(tests[i], b), mse(tests[i], b), mape(tests[i], b) ]
    add_row(row)

MAE of Naive Seasonal Model forecasting horizon = 1: 26.044376373291016
RMSE of Naive Seasonal Model forecasting horizon = 1: 40.86237335205078
MSE of Naive Seasonal Model forecasting horizon = 1: 1669.733642578125
MAPE of Naive Seasonal Model forecasting horizon = 1: 5.199010670185089


MAE of Naive Seasonal Model forecasting horizon = 7: 26.396310806274414
RMSE of Naive Seasonal Model forecasting horizon = 7: 41.312774658203125
MSE of Naive Seasonal Model forecasting horizon = 7: 1706.7452392578125
MAPE of Naive Seasonal Model forecasting horizon = 7: 5.238295346498489


MAE of Naive Seasonal Model forecasting horizon = 30: 67.06342315673828
RMSE of Naive Seasonal Model forecasting horizon = 30: 92.5423583984375
MSE of Naive Seasonal Model forecasting horizon = 30: 8564.087890625
MAPE of Naive Seasonal Model forecasting horizon = 30: 12.882056832313538


MAE of Naive Seasonal Model forecasting horizon = 90: 106.08699035644531
RMSE of Naive Seasonal Model forecasting horizon = 90: 142

# Random Forest

In [24]:
from darts.models import RandomForest

def create_RF():
  return RandomForest(
      lags=[-i for i in range(1, 31)] + [-90, -180],  # Short-term and long-term lags
      lags_past_covariates=[-i for i in range(1, 31)] + [-90, -180],
      n_estimators=100,  # Number of trees in the forest
      max_depth=15,  # Maximum depth of each tree
  )

# Backtesting Random Forest

In [26]:
backtesting_RF = [[], [], []]
for t in targets_scaled:
  RF_model = create_RF()
  RF_model.fit(trains_scaled[targets_scaled.index(t)], past_covariates = past_covs_scaled[targets_scaled.index(t)])
  for h in bt_horizons:
    hist_RF = RF_model.historical_forecasts(
            t,
            past_covariates = past_covs_scaled[targets_scaled.index(t)],
            start=tests_scaled[targets_scaled.index(t)].time_index[0] - timedelta(days=h),
            forecast_horizon=h,
            stride=1,
            verbose=True,
            retrain=False
      )

    hist_predict_RF = scalers[targets_scaled.index(t)].inverse_transform(hist_RF)
    backtesting_RF[targets_scaled.index(t)].append(hist_predict_RF)

100%|██████████| 495/495 [03:19<00:00,  2.48it/s]


In [ ]:
for i in range(3):
  for b in backtesting_RF[i]:
    h = bt_horizons[backtesting_RF[i].index(b)]
    print_graph_backtesting(tests[i], b, True, 'Random Forest',h)

In [ ]:
add_row(['Backtesting Random Forest','','','',''])
for i in range(3):
  add_row([f'time period = {i + 1}', '', '', '', ''])
  for b in backtesting_RF[i]:
    print(f"MAE of RF forecasting horizon = {bt_horizons[backtesting_RF[i].index(b)]}: {mae(tests[i], b)}")
    print(f"RMSE of RF forecasting horizon = {bt_horizons[backtesting_RF[i].index(b)]}: {rmse(tests[i], b)}")
    print(f"MSE of RF forecasting horizon = {bt_horizons[backtesting_RF[i].index(b)]}: {mse(tests[i], b)}")
    print(f"MAPE of RF forecasting horizon = {bt_horizons[backtesting_RF[i].index(b)]}: {mape(tests[i], b)}")
    print("\n")
    row = [f'Random Forest fh={bt_horizons[backtesting_RF[i].index(b)]}', mae(tests[i], b), rmse(tests[i], b), mse(tests[i], b), mape(tests[i], b) ]
    add_row(row)

MAE of RF forecasting horizon = 1: 14.890245863822232
RMSE of RF forecasting horizon = 1: 21.6615396347396
MSE of RF forecasting horizon = 1: 469.22229934739465
MAPE of RF forecasting horizon = 1: 3.0106220774629455


MAE of RF forecasting horizon = 7: 19.354018938358553
RMSE of RF forecasting horizon = 7: 27.532893536336168
MSE of RF forecasting horizon = 7: 758.060226483222
MAPE of RF forecasting horizon = 7: 3.8817434484574616


MAE of RF forecasting horizon = 30: 19.104535123257776
RMSE of RF forecasting horizon = 30: 27.66717629013433
MSE of RF forecasting horizon = 30: 765.4726438693712
MAPE of RF forecasting horizon = 30: 3.7406497903921303


MAE of RF forecasting horizon = 90: 19.395536885967815
RMSE of RF forecasting horizon = 90: 29.41738830002998
MSE of RF forecasting horizon = 90: 865.3827343947409
MAPE of RF forecasting horizon = 90: 3.4969531890037806


MAE of RF forecasting horizon = 1: 49.69006118556815
RMSE of RF forecasting horizon = 1: 76.59139686282506
MSE of RF for

# LSTM Model

In [ ]:
from darts.models import TCNModel, BlockRNNModel, TransformerModel, TFTModel


In [ ]:
def create_LSTM():
  return BlockRNNModel(
      input_chunk_length=21,
      output_chunk_length=7,
      hidden_dim=104,
      model='LSTM',
      n_rnn_layers=4,
      dropout=0.18390991552139796,
      optimizer_kwargs={'lr': 0.00014678997505613995},
  )

In [ ]:
backtesting_LSTM = [[], [], []]

for t in targets_scaled:
  LSTM_model = create_LSTM()
  LSTM_model.fit(trains_scaled[targets_scaled.index(t)], past_covariates = past_covs_scaled[targets_scaled.index(t)])
  for h in bt_horizons:
    hist_LSTM = LSTM_model.historical_forecasts(
            t,
            past_covariates = past_covs_scaled[targets_scaled.index(t)],
            start=tests_scaled[targets_scaled.index(t)].time_index[0],
            forecast_horizon=h,
            stride=1,
            verbose=True,
            retrain=False
      )

    hist_predict_LSTM = scalers[targets_scaled.index(t)].inverse_transform(hist_LSTM)
    backtesting_LSTM[targets_scaled.index(t)].append(hist_predict_LSTM)

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name          | Type             | Params
---------------------------------------------------
0 | criterion     | MSELoss          | 0     
1 | train_metrics | MetricCollection | 0     
2 | val_metrics   | MetricCollection | 0     
3 | rnn           | LSTM             | 309 K 
4 | fc            | Sequential       | 735   
---------------------------------------------------
310 K     Trainable params
0         Non-trainable params
310 K     Total params
1.241     Total estimated model params size (MB)


Training: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=100` reached.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


...

Predicting: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

In [ ]:
for i in range(3):
  for b in backtesting_LSTM[i]:
    h = bt_horizons[backtesting_LSTM[i].index(b)]
    print_graph_backtesting(tests[i], b, True, 'LSTM model',h)

In [ ]:
add_row(['Backtesting LSTM Model','','','',''])
for i in range(3):
  add_row([f'time period = {i + 1}', '', '', '', ''])
  for b in backtesting_LSTM[i]:
    print(f"MAE of LSTM forecasting horizon = {bt_horizons[backtesting_LSTM[i].index(b)]}: {mae(tests[i], b)}")
    print(f"RMSE of LSTM forecasting horizon = {bt_horizons[backtesting_LSTM[i].index(b)]}: {rmse(tests[i], b)}")
    print(f"MSE of LSTM forecasting horizon = {bt_horizons[backtesting_LSTM[i].index(b)]}: {mse(tests[i], b)}")
    print(f"MAPE of LSTM forecasting horizon = {bt_horizons[backtesting_LSTM[i].index(b)]}: {mape(tests[i], b)}")
    print("\n")
    row = [f'LSTM fh={bt_horizons[backtesting_LSTM[i].index(b)]}', mae(tests[i], b), rmse(tests[i], b), mse(tests[i], b), mape(tests[i], b) ]
    add_row(row)

MAE of LSTM forecasting horizon = 1: 61.326446533203125
RMSE of LSTM forecasting horizon = 1: 83.34935760498047
MSE of LSTM forecasting horizon = 1: 6947.115234375
MAPE of LSTM forecasting horizon = 1: 11.748217791318893


MAE of LSTM forecasting horizon = 7: 81.73197174072266
RMSE of LSTM forecasting horizon = 7: 106.9529800415039
MSE of LSTM forecasting horizon = 7: 11438.939453125
MAPE of LSTM forecasting horizon = 7: 15.631644427776337


MAE of LSTM forecasting horizon = 30: 108.10504150390625
RMSE of LSTM forecasting horizon = 30: 132.9635009765625
MSE of LSTM forecasting horizon = 30: 17679.291015625
MAPE of LSTM forecasting horizon = 30: 20.769919455051422


MAE of LSTM forecasting horizon = 90: 148.89865112304688
RMSE of LSTM forecasting horizon = 90: 164.481201171875
MSE of LSTM forecasting horizon = 90: 27054.064453125
MAPE of LSTM forecasting horizon = 90: 28.229692578315735


MAE of LSTM forecasting horizon = 1: 107.00281524658203
RMSE of LSTM forecasting horizon = 1: 144.7

# VanillaRNN Model

In [ ]:
def create_vanillaRNN():
  return BlockRNNModel(
      input_chunk_length=21,
      output_chunk_length=7,
      model='RNN',
      hidden_dim=31,
      n_rnn_layers=1,
      dropout=0.34008569567908437,
      optimizer_kwargs={'lr': 0.0009241588491743642},
  )

In [ ]:
backtesting_VanillaRNN = [[], [], []]

for t in targets_scaled:
  vanillaRNN_model = create_vanillaRNN()
  vanillaRNN_model.fit(trains_scaled[targets_scaled.index(t)], past_covariates = past_covs_scaled[targets_scaled.index(t)])
  for h in bt_horizons:
    hist_VanillaRNN = vanillaRNN_model.historical_forecasts(
            t,
            past_covariates = past_covs_scaled[targets_scaled.index(t)],
            start=tests_scaled[targets_scaled.index(t)].time_index[0],
            forecast_horizon=h,
            stride=1,
            verbose=True,
            retrain=False
      )

    hist_predict_VanillaRNN = scalers[targets_scaled.index(t)].inverse_transform(hist_VanillaRNN)
    backtesting_VanillaRNN[targets_scaled.index(t)].append(hist_predict_VanillaRNN)

/usr/local/lib/python3.10/dist-packages/torch/nn/modules/rnn.py:82: UserWarning:

dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.34008569567908437 and num_layers=1

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name          | Type             | Params
---------------------------------------------------
0 | criterion     | MSELoss          | 0     
1 | train_metrics | MetricCollection | 0     
2 | val_metrics   | MetricCollection | 0     
3 | rnn           | RNN              | 1.3 K 
4 | fc  

Training: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=100` reached.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


...

Predicting: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

In [ ]:
for i in range(3):
  for b in backtesting_VanillaRNN[i]:
    h = bt_horizons[backtesting_VanillaRNN[i].index(b)]
    print_graph_backtesting(tests[i], b, True, 'Vanilla RNN',h)

In [ ]:
add_row(['Backtesting RNN Model','','','',''])
for i in range(3):
  add_row([f'time period = {i + 1}', '', '', '', ''])
  for b in backtesting_VanillaRNN[i]:
    print(f"MAE of RNN forecasting horizon = {bt_horizons[backtesting_VanillaRNN[i].index(b)]}: {mae(tests[i], b)}")
    print(f"RMSE of RNN forecasting horizon = {bt_horizons[backtesting_VanillaRNN[i].index(b)]}: {rmse(tests[i], b)}")
    print(f"MSE of RNN forecasting horizon = {bt_horizons[backtesting_VanillaRNN[i].index(b)]}: {mse(tests[i], b)}")
    print(f"MAPE of RNN forecasting horizon = {bt_horizons[backtesting_VanillaRNN[i].index(b)]}: {mape(tests[i], b)}")
    print("\n")
    row = [f'RNN fh={bt_horizons[backtesting_VanillaRNN[i].index(b)]}', mae(tests[i], b), rmse(tests[i], b), mse(tests[i], b), mape(tests[i], b) ]
    add_row(row)

MAE of RNN forecasting horizon = 1: 29.172576904296875
RMSE of RNN forecasting horizon = 1: 39.40338134765625
MSE of RNN forecasting horizon = 1: 1552.6263427734375
MAPE of RNN forecasting horizon = 1: 5.825793743133545


MAE of RNN forecasting horizon = 7: 56.53422546386719
RMSE of RNN forecasting horizon = 7: 80.90036010742188
MSE of RNN forecasting horizon = 7: 6544.8681640625
MAPE of RNN forecasting horizon = 7: 11.02626547217369


MAE of RNN forecasting horizon = 30: 71.16918182373047
RMSE of RNN forecasting horizon = 30: 98.9444808959961
MSE of RNN forecasting horizon = 30: 9790.0107421875
MAPE of RNN forecasting horizon = 30: 13.503801822662354


MAE of RNN forecasting horizon = 90: 96.97294616699219
RMSE of RNN forecasting horizon = 90: 122.30156707763672
MSE of RNN forecasting horizon = 90: 14957.6728515625
MAPE of RNN forecasting horizon = 90: 17.45474487543106


MAE of RNN forecasting horizon = 1: 67.88179779052734
RMSE of RNN forecasting horizon = 1: 78.84271240234375
MSE o

# GRU Model

In [ ]:
def create_GRU():
  return BlockRNNModel(
      input_chunk_length=21,
      output_chunk_length=7,
      model='GRU',
      hidden_dim=75,
      n_rnn_layers=1,
      dropout=0.007824503730612165,
      optimizer_kwargs={'lr': 0.000566687831423731},
  )

In [ ]:
backtesting_GRU = [[], [], []]

for t in targets_scaled:
  GRU_model = create_GRU()
  GRU_model.fit(trains_scaled[targets_scaled.index(t)], past_covariates = past_covs_scaled[targets_scaled.index(t)])
  for h in bt_horizons:
    hist_GRU = GRU_model.historical_forecasts(
            t,
            past_covariates = past_covs_scaled[targets_scaled.index(t)],
            start=tests_scaled[targets_scaled.index(t)].time_index[0],
            forecast_horizon=h,
            stride=1,
            verbose=True,
            retrain=False
      )

    hist_predict_GRU = scalers[targets_scaled.index(t)].inverse_transform(hist_GRU)
    backtesting_GRU[targets_scaled.index(t)].append(hist_predict_GRU)

/usr/local/lib/python3.10/dist-packages/torch/nn/modules/rnn.py:82: UserWarning:

dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.007824503730612165 and num_layers=1

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name          | Type             | Params
---------------------------------------------------
0 | criterion     | MSELoss          | 0     
1 | train_metrics | MetricCollection | 0     
2 | val_metrics   | MetricCollection | 0     
3 | rnn           | GRU              | 19.1 K
4 | fc 

Training: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=100` reached.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


...

Predicting: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

In [ ]:
for i in range(3):
  for b in backtesting_GRU[i]:
    h = bt_horizons[backtesting_GRU[i].index(b)]
    print_graph_backtesting(tests[i], b, True, 'GRU model',h)

In [ ]:
add_row(['Backtesting GRU Model','','','',''])
for i in range(3):
  add_row([f'time period = {i + 1}', '', '', '', ''])
  for b in backtesting_GRU[i]:
    print(f"MAE of GRU forecasting horizon = {bt_horizons[backtesting_GRU[i].index(b)]}: {mae(tests[i], b)}")
    print(f"RMSE of GRU forecasting horizon = {bt_horizons[backtesting_GRU[i].index(b)]}: {rmse(tests[i], b)}")
    print(f"MSE of GRU forecasting horizon = {bt_horizons[backtesting_GRU[i].index(b)]}: {mse(tests[i], b)}")
    print(f"MAPE of GRU forecasting horizon = {bt_horizons[backtesting_GRU[i].index(b)]}: {mape(tests[i], b)}")
    print("\n")
    row = [f'GRU fh={bt_horizons[backtesting_GRU[i].index(b)]}', mae(tests[i], b), rmse(tests[i], b), mse(tests[i], b), mape(tests[i], b) ]
    add_row(row)

MAE of GRU forecasting horizon = 1: 43.79555130004883
RMSE of GRU forecasting horizon = 1: 51.438690185546875
MSE of GRU forecasting horizon = 1: 2645.938720703125
MAPE of GRU forecasting horizon = 1: 8.935849368572235


MAE of GRU forecasting horizon = 7: 154.1761474609375
RMSE of GRU forecasting horizon = 7: 171.80235290527344
MSE of GRU forecasting horizon = 7: 29516.046875
MAPE of GRU forecasting horizon = 7: 31.888654828071594


MAE of GRU forecasting horizon = 30: 203.83790588378906
RMSE of GRU forecasting horizon = 30: 223.63491821289062
MSE of GRU forecasting horizon = 30: 50012.578125
MAPE of GRU forecasting horizon = 30: 41.262972354888916


MAE of GRU forecasting horizon = 90: 255.70213317871094
RMSE of GRU forecasting horizon = 90: 271.472900390625
MSE of GRU forecasting horizon = 90: 73697.5390625
MAPE of GRU forecasting horizon = 90: 49.43547546863556


MAE of GRU forecasting horizon = 1: 29.019418716430664
RMSE of GRU forecasting horizon = 1: 40.590980529785156
MSE of GR

# Transformer Model

In [ ]:
def create_Transformer():
  return TransformerModel(
      input_chunk_length = 21,
      output_chunk_length = 7,
      d_model=88,
      nhead=4,
      num_encoder_layers=4,
      num_decoder_layers=1,
      dropout=0.14295488378943239,
      optimizer_kwargs={'lr': 0.00046254166100837376},
  )

In [ ]:
backtesting_Transformer = [[], [], []]

for t in targets_scaled:
  transformer_model = create_Transformer()
  transformer_model.fit(trains_scaled[targets_scaled.index(t)], past_covariates = past_covs_scaled[targets_scaled.index(t)])
  for h in bt_horizons:
    hist_Transformer = transformer_model.historical_forecasts(
            t,
            past_covariates = past_covs_scaled[targets_scaled.index(t)],
            start=tests_scaled[targets_scaled.index(t)].time_index[0],
            forecast_horizon=h,
            stride=1,
            verbose=True,
            retrain=False
      )

    hist_predict_Transformer = scalers[targets_scaled.index(t)].inverse_transform(hist_Transformer)
    backtesting_Transformer[targets_scaled.index(t)].append(hist_predict_Transformer)

/usr/local/lib/python3.10/dist-packages/torch/nn/modules/transformer.py:282: UserWarning:

enable_nested_tensor is True, but self.use_nested_tensor is False because encoder_layer.self_attn.batch_first was not True(use batch_first for better inference performance)

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name                | Type                | Params
------------------------------------------------------------
0 | criterion           | MSELoss             | 0     
1 | train_metrics       | MetricCollection    | 0     
2 | val_metrics         | MetricCollection    | 0     

Training: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=100` reached.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


...

Predicting: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

In [ ]:
for i in range(3):
  for b in backtesting_Transformer[i]:
    h = bt_horizons[backtesting_Transformer[i].index(b)]
    print_graph_backtesting(tests[i], b, True, 'Transformer Model',h)

In [ ]:
add_row(['Backtesting Transformer Model','','','',''])
for i in range(3):
  add_row([f'time period = {i + 1}', '', '', '', ''])
  for b in backtesting_Transformer[i]:
    print(f"MAE of Transformer Model forecasting horizon = {bt_horizons[backtesting_Transformer[i].index(b)]}: {mae(tests[i], b)}")
    print(f"RMSE of Transformer Model forecasting horizon = {bt_horizons[backtesting_Transformer[i].index(b)]}: {rmse(tests[i], b)}")
    print(f"MSE of Transformer Model forecasting horizon = {bt_horizons[backtesting_Transformer[i].index(b)]}: {mse(tests[i], b)}")
    print(f"MAPE of Transformer Model forecasting horizon = {bt_horizons[backtesting_Transformer[i].index(b)]}: {mape(tests[i], b)}")
    print("\n")
    row = [f'Transformer fh={bt_horizons[backtesting_Transformer[i].index(b)]}', mae(tests[i], b), rmse(tests[i], b), mse(tests[i], b), mape(tests[i], b) ]
    add_row(row)

MAE of Transformer Model forecasting horizon = 1: 84.33323669433594
RMSE of Transformer Model forecasting horizon = 1: 92.91423034667969
MSE of Transformer Model forecasting horizon = 1: 8633.0537109375
MAPE of Transformer Model forecasting horizon = 1: 17.54244565963745


MAE of Transformer Model forecasting horizon = 7: 120.70269775390625
RMSE of Transformer Model forecasting horizon = 7: 133.31741333007812
MSE of Transformer Model forecasting horizon = 7: 17773.53125
MAPE of Transformer Model forecasting horizon = 7: 24.758702516555786


MAE of Transformer Model forecasting horizon = 30: 166.8392791748047
RMSE of Transformer Model forecasting horizon = 30: 183.05328369140625
MSE of Transformer Model forecasting horizon = 30: 33508.50390625
MAPE of Transformer Model forecasting horizon = 30: 33.651572465896606


MAE of Transformer Model forecasting horizon = 90: 194.71746826171875
RMSE of Transformer Model forecasting horizon = 90: 208.85964965820312
MSE of Transformer Model forecast

# TFT Model

In [ ]:
def create_TFT():
  return TFTModel(
      input_chunk_length=21,
      output_chunk_length=7,
      hidden_size=30,
      lstm_layers=1,
      num_attention_heads=4,
      dropout=0.06118422728497173,
      hidden_continuous_size=10,
      optimizer_kwargs={'lr': 0.005081664304452033},
  )

In [ ]:
backtesting_TFT = [[], [], []]

for t in targets_scaled:
  TFT_model = create_TFT()
  TFT_model.fit(trains_scaled[targets_scaled.index(t)],
                past_covariates = past_covs_scaled[targets_scaled.index(t)],
                future_covariates = future_covs_scaled[targets_scaled.index(t)])
  for h in bt_horizons:
    hist_TFT = TFT_model.historical_forecasts(
            t,
            past_covariates = past_covs_scaled[targets_scaled.index(t)],
            future_covariates = future_covs_scaled[targets_scaled.index(t)],
            start=tests_scaled[targets_scaled.index(t)].time_index[0],
            forecast_horizon=h,
            stride=1,
            verbose=True,
            retrain=False
      )

    hist_predict_TFT = scalers[targets_scaled.index(t)].inverse_transform(hist_TFT)
    backtesting_TFT[targets_scaled.index(t)].append(hist_predict_TFT)

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
   | Name                              | Type                             | Params
----------------------------------------------------------------------------------------
0  | train_metrics                     | MetricCollection                 | 0     
1  | val_metrics                       | MetricCollection                 | 0     
2  | input_embeddings                  | _MultiEmbedding                  | 0     
3  | static_covariates_vsn             | _VariableSelectionNetwork        | 0     
4  | encoder_vsn                       | 

Training: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=100` reached.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


...

Predicting: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

In [ ]:
for i in range(3):
  for b in backtesting_TFT[i]:
    h = bt_horizons[backtesting_TFT[i].index(b)]
    print_graph_backtesting(tests[i], b, True, 'TFT Model',h)

In [ ]:
add_row(['Backtesting TFT Model','','','',''])
for i in range(3):
  add_row([f'time period = {i + 1}', '', '', '', ''])
  for b in backtesting_TFT[i]:
    print(f"MAE of TFT Model forecasting horizon = {bt_horizons[backtesting_TFT[i].index(b)]}: {mae(tests[i], b)}")
    print(f"RMSE of TFT Model forecasting horizon = {bt_horizons[backtesting_TFT[i].index(b)]}: {rmse(tests[i], b)}")
    print(f"MSE of TFT Model forecasting horizon = {bt_horizons[backtesting_TFT[i].index(b)]}: {mse(tests[i], b)}")
    print(f"MAPE of TFT Model forecasting horizon = {bt_horizons[backtesting_TFT[i].index(b)]}: {mape(tests[i], b)}")
    print("\n")
    row = [f'TFT fh={bt_horizons[backtesting_TFT[i].index(b)]}', mae(tests[i], b), rmse(tests[i], b), mse(tests[i], b), mape(tests[i], b) ]
    add_row(row)

MAE of TFT Model forecasting horizon = 1: 32.01123046875
RMSE of TFT Model forecasting horizon = 1: 40.20191955566406
MSE of TFT Model forecasting horizon = 1: 1616.1943359375
MAPE of TFT Model forecasting horizon = 1: 7.009085267782211


MAE of TFT Model forecasting horizon = 7: 57.22621536254883
RMSE of TFT Model forecasting horizon = 7: 73.22470092773438
MSE of TFT Model forecasting horizon = 7: 5361.8564453125
MAPE of TFT Model forecasting horizon = 7: 12.576138973236084


MAE of TFT Model forecasting horizon = 30: 50.600433349609375
RMSE of TFT Model forecasting horizon = 30: 67.07716369628906
MSE of TFT Model forecasting horizon = 30: 4499.34619140625
MAPE of TFT Model forecasting horizon = 30: 11.079813539981842


MAE of TFT Model forecasting horizon = 90: 46.255775451660156
RMSE of TFT Model forecasting horizon = 90: 61.29167556762695
MSE of TFT Model forecasting horizon = 90: 3756.66943359375
MAPE of TFT Model forecasting horizon = 90: 9.172084927558899


MAE of TFT Model fore

# NBEATS Model

In [ ]:
from darts.models import NBEATSModel

def create_NBEATS():
  return NBEATSModel(
      input_chunk_length=21,
      output_chunk_length=7,
      num_stacks=19,
      num_blocks=4,
      num_layers=4,
      layer_widths=378,
      expansion_coefficient_dim=8,
      dropout=0.007293860107310261,
      add_encoders =  {
          'cyclic': {'past': ['month', 'dayofweek', 'dayofyear']},  # Capture seasonal trends
          'datetime_attribute': {'past': ['day', 'week', 'year']},
          'position': {'past': ['relative']},
          'transformer': Scaler(),
      },
      optimizer_kwargs={'lr': 0.0005903374698873167},
  )

In [ ]:
backtesting_NBEATS = [[], [], []]

for t in targets_scaled:
  NBEATS_model = create_NBEATS()
  NBEATS_model.fit(trains_scaled[targets_scaled.index(t)], past_covariates = past_covs_scaled[targets_scaled.index(t)])
  for h in bt_horizons:
    hist_NBEATS = NBEATS_model.historical_forecasts(
            t,
            past_covariates = past_covs_scaled[targets_scaled.index(t)],
            start=tests_scaled[targets_scaled.index(t)].time_index[0],
            forecast_horizon=h,
            stride=1,
            verbose=True,
            retrain=False
      )

    hist_predict_NBEATS = scalers[targets_scaled.index(t)].inverse_transform(hist_NBEATS)
    backtesting_NBEATS[targets_scaled.index(t)].append(hist_predict_NBEATS)

INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.callbacks.model_summary:
  | Name          | Type             | Params
---------------------------------------------------
0 | criterion     | MSELoss          | 0     
1 | train_metrics | MetricCollection | 0     
2 | val_metrics   | MetricCollection | 0     
3 | stacks        | ModuleList       | 44.4 M
---------------------------------------------------
44.4 M    Trainable params
6.4 K     Non-trainable params
44.4 M    Total params
177.429   Total estimated model params size (MB)


Training: |          | 0/? [00:00<?, ?it/s]

In [ ]:
for i in range(3):
  for b in backtesting_NBEATS[i]:
    h = bt_horizons[backtesting_NBEATS[i].index(b)]
    print_graph_backtesting(tests[i], b, True, 'NBEATS Model',h)

In [ ]:
add_row(['Backtesting NBEATS Model','','','',''])
for i in range(3):
  add_row([f'time period = {i + 1}', '', '', '', ''])
  for b in backtesting_NBEATS[i]:
    print(f"MAE of NBEATS Model forecasting horizon = {bt_horizons[backtesting_NBEATS[i].index(b)]}: {mae(tests[i], b)}")
    print(f"RMSE of NBEATS Model forecasting horizon = {bt_horizons[backtesting_NBEATS[i].index(b)]}: {rmse(tests[i], b)}")
    print(f"MSE of NBEATS Model forecasting horizon = {bt_horizons[backtesting_NBEATS[i].index(b)]}: {mse(tests[i], b)}")
    print(f"MAPE of NBEATS Model forecasting horizon = {bt_horizons[backtesting_NBEATS[i].index(b)]}: {mape(tests[i], b)}")
    print("\n")
    row = [f'NBEATS fh={bt_horizons[backtesting_NBEATS[i].index(b)]}', mae(tests[i], b), rmse(tests[i], b), mse(tests[i], b), mape(tests[i], b) ]
    add_row(row)

# TCN Model

In [ ]:
def create_TCN():
  return TCNModel(
      input_chunk_length=21,
      output_chunk_length=7,
      kernel_size=8,
      num_filters=36,
      weight_norm= False,
      dilation_base=2,
      dropout= 0.14321708644925318,
      optimizer_kwargs={'lr': 0.0005056311276120884},
      random_state=0,
      add_encoders = {
          'cyclic': {'past': ['month', 'dayofweek', 'dayofyear']},  # Capture seasonal trends
          'datetime_attribute': {'past': ['day', 'week', 'year']},
          'position': {'past': ['relative']},
          'transformer': Scaler(),
      }
  )

In [ ]:
backtesting_TCN = [[], [], []]

for i in range(3):
  TCN_model = create_TCN()
  TCN_model.fit(trains_scaled[targets_scaled.index(t)], past_covariates = past_covs_scaled[targets_scaled.index(t)])
  for h in bt_horizons:
    hist_TCN = TCN_model.historical_forecasts(
            t,
            past_covariates = past_covs_scaled[targets_scaled.index(t)],
            start=tests_scaled[targets_scaled.index(t)].time_index[0],
            forecast_horizon=h,
            stride=1,
            verbose=True,
            retrain=False
      )

    hist_predict_TCN = scalers[targets_scaled.index(t)].inverse_transform(hist_TCN)
    backtesting_TCN[targets_scaled.index(t)].append(hist_predict_TCN)

NameError: name 'TCNModel' is not defined

In [ ]:
for i in range(3):
  for b in backtesting_TCN[i]:
    h = bt_horizons[backtesting_TCN[i].index(b)]
    print_graph_backtesting(tests[i], b, True, 'TCN Model',h)

In [ ]:
add_row(['Backtesting TCN Model','','','',''])
for i in range(3):
  add_row([f'time period = {i + 1}', '', '', '', ''])
  for b in backtesting_TCN[i]:
    print(f"MAE of TCN Model forecasting horizon = {bt_horizons[backtesting_TCN[i].index(b)]}: {mae(tests[i], b)}")
    print(f"RMSE of TCN Model forecasting horizon = {bt_horizons[backtesting_TCN[i].index(b)]}: {rmse(tests[i], b)}")
    print(f"MSE of TCN Model forecasting horizon = {bt_horizons[backtesting_TCN[i].index(b)]}: {mse(tests[i], b)}")
    print(f"MAPE of TCN Model forecasting horizon = {bt_horizons[backtesting_TCN[i].index(b)]}: {mape(tests[i], b)}")
    print("\n")
    row = [f'TCN fh={bt_horizons[backtesting_TCN[i].index(b)]}', mae(tests[i], b), rmse(tests[i], b), mse(tests[i], b), mape(tests[i], b) ]
    add_row(row)

# LightGBM Model

In [ ]:
from darts.models.forecasting.lgbm import LightGBMModel

def create_LightGBM():
  return LightGBMModel(
      lags=[-i for i in range(1, 31)] + [-90, -180],  # Short-term and long-term lags
      lags_past_covariates=[-i for i in range(1, 31)] + [-90, -180],
      output_chunk_length = 7,
  )

In [ ]:
backtesting_Transformer = [[], [], []]

for t in targets_scaled:
  transformer_model = create_Transformer()
  transformer_model.fit(trains_scaled[targets_scaled.index(t)], past_covariates = past_covs_scaled[targets_scaled.index(t)])
  for h in bt_horizons:
    hist_Transformer = transformer_model.historical_forecasts(
            t,
            past_covariates = past_covs_scaled[targets_scaled.index(t)],
            start=tests_scaled[targets_scaled.index(t)].time_index[0],
            forecast_horizon=h,
            stride=1,
            verbose=True,
            retrain=False
      )

    hist_predict_Transformer = scalers[targets_scaled.index(t)].inverse_transform(hist_Transformer)
    backtesting_Transformer[targets_scaled.index(t)].append(hist_predict_Transformer)

In [ ]:
backtesting_LightGBM = [[], [], []]
for t in targets_scaled:
  LightGBM_model = create_LightGBM()
  LightGBM_model.fit(trains_scaled[targets_scaled.index(t)], past_covariates = past_covs_scaled[targets_scaled.index(t)])
  for h in bt_horizons:
    hist_LightGBM = LightGBM_model.historical_forecasts(
            t,
            past_covariates =  past_covs_scaled[targets_scaled.index(t)],
            start=tests_scaled[targets_scaled.index(t)].time_index[0],
            forecast_horizon=h,
            stride=1,
            verbose=True,
            retrain=False
      )
    hist_predict_LightGBM = scalers[targets_scaled.index(t)].inverse_transform(hist_LightGBM)
    backtesting_LightGBM[targets_scaled.index(t)].append(hist_predict_LightGBM)

In [ ]:
for i in range(3):
  for b in backtesting_LightGBM[i]:
    h = bt_horizons[backtesting_LightGBM[i].index(b)]
    print_graph_backtesting(tests[i], b, True, 'LightGBM Model',h)

In [ ]:
add_row(['Backtesting LightGBM Model','','','',''])
for i in range(3):
  add_row([f'time period = {i + 1}', '', '', '', ''])
  for b in backtesting_LightGBM[i]:
    print(f"MAE of LightGBM forecasting horizon = {bt_horizons[backtesting_LightGBM[i].index(b)]}: {mae(tests[i], b)}")
    print(f"RMSE of LightGBM forecasting horizon = {bt_horizons[backtesting_LightGBM[i].index(b)]}: {rmse(tests[i], b)}")
    print(f"MSE of LightGBM forecasting horizon = {bt_horizons[backtesting_LightGBM[i].index(b)]}: {mse(tests[i], b)}")
    print(f"MAPE of LightGBM forecasting horizon = {bt_horizons[backtesting_LightGBM[i].index(b)]}: {mape(tests[i], b)}")
    print("\n")
    row = [f'LightGBM fh={bt_horizons[backtesting_LightGBM[i].index(b)]}', mae(tests[i], b), rmse(tests[i], b), mse(tests[i], b), mape(tests[i], b) ]
    add_row(row)

# XGB Model

In [ ]:
from darts.models import XGBModel

def create_XGB():
  return XGBModel (
      lags=[-i for i in range(1, 31)] + [-90, -180],  # Short-term and long-term lags
      lags_past_covariates=[-i for i in range(1, 31)] + [-90, -180],
      output_chunk_length = 7,
  )

In [ ]:
backtesting_LightGBM = [[], [], []]
for t in targets_scaled:
  LightGBM_model = create_LightGBM()
  LightGBM_model.fit(trains_scaled[targets_scaled.index(t)], past_covariates = past_covs_scaled[targets_scaled.index(t)])
  for h in bt_horizons:
    hist_LightGBM = LightGBM_model.historical_forecasts(
            t,
            past_covariates =  past_covs_scaled[targets_scaled.index(t)],
            start=tests_scaled[targets_scaled.index(t)].time_index[0],
            forecast_horizon=h,
            stride=1,
            verbose=True,
            retrain=False
      )
    hist_predict_LightGBM = scalers[targets_scaled.index(t)].inverse_transform(hist_LightGBM)
    backtesting_LightGBM[targets_scaled.index(t)].append(hist_predict_LightGBM)

In [ ]:
backtesting_XGB = [[], [], []]

for t in targets_scaled:
  XGB_model = create_XGB()
  XGB_model.fit(trains_scaled[targets_scaled.index(t)], past_covariates = past_covs_scaled[targets_scaled.index(t)])
  for h in bt_horizons:
    hist_XGB = XGB_model.historical_forecasts(
            t,
            past_covariates = past_covs_scaled[targets_scaled.index(t)],
            start = tests_scaled[targets_scaled.index(t)].time_index[0],
            forecast_horizon=h,
            stride=1,
            verbose=True,
            retrain=False
      )

    hist_predict_XGB = scalers[targets_scaled.index(t)].inverse_transform(hist_XGB)
    backtesting_XGB[targets_scaled.index(t)].append(hist_predict_XGB)

In [ ]:
for i in range(3):
  for b in backtesting_XGB[i]:
    h = bt_horizons[backtesting_XGB[i].index(b)]
    print_graph_backtesting(tests[i], b, True, 'XGB Model',h)

In [ ]:
add_row(['Backtesting XGB Model','','','',''])
for i in range(3):
  add_row([f'time period = {i + 1}', '', '', '', ''])
  for b in backtesting_XGB[i]:
    print(f"MAE of XGB forecasting horizon = {bt_horizons[backtesting_XGB[i].index(b)]}: {mae(tests[i], b)}")
    print(f"RMSE of XGB forecasting horizon = {bt_horizons[backtesting_XGB[i].index(b)]}: {rmse(tests[i], b)}")
    print(f"MSE of XGB forecasting horizon = {bt_horizons[backtesting_XGB[i].index(b)]}: {mse(tests[i], b)}")
    print(f"MAPE of XGB forecasting horizon = {bt_horizons[backtesting_XGB[i].index(b)]}: {mape(tests[i], b)}")
    print("\n")
    row = [f'XGB fh={bt_horizons[backtesting_XGB[i].index(b)]}', mae(tests[i], b), rmse(tests[i], b), mse(tests[i], b), mape(tests[i], b) ]
    add_row(row)

# CatBoost Model

In [ ]:
from darts.models import CatBoostModel

def create_CatBoost():
  return CatBoostModel(
      lags=[-i for i in range(1, 31)] + [-90, -180],  # Short-term and long-term lags
      lags_past_covariates=[-i for i in range(1, 31)] + [-90, -180],
      output_chunk_length = 7,
  )

In [ ]:
backtesting_XGB = [[], [], []]

for t in targets_scaled:
  XGB_model = create_XGB()
  XGB_model.fit(trains_scaled[targets_scaled.index(t)], past_covariates = past_covs_scaled[targets_scaled.index(t)])
  for h in bt_horizons:
    hist_XGB = XGB_model.historical_forecasts(
            t,
            past_covariates = past_covs_scaled[targets_scaled.index(t)],
            start = tests_scaled[targets_scaled.index(t)].time_index[0],
            forecast_horizon=h,
            stride=1,
            verbose=True,
            retrain=False
      )

    hist_predict_XGB = scalers[targets_scaled.index(t)].inverse_transform(hist_XGB)
    backtesting_XGB[targets_scaled.index(t)].append(hist_predict_XGB)

In [ ]:
backtesting_CatBoost = [[], [], []]

for t in targets_scaled:
  CatBoost_model = create_CatBoost()
  CatBoost_model.fit(trains_scaled[targets_scaled.index(t)], past_covariates = past_covs_scaled[targets_scaled.index(t)])
  for h in bt_horizons:
    hist_CatBoost = CatBoost_model.historical_forecasts(
            t,
            past_covariates = past_covs_scaled[targets_scaled.index(t)],
            start=tests_scaled[targets_scaled.index(t)].time_index[0],,
            forecast_horizon=h,
            stride=1,
            verbose=True,
            retrain=False
      )

    hist_predict_CatBoost = [targets_scaled.index(t)].inverse_transform(hist_CatBoost)
    backtesting_CatBoost[targets_scaled.index(t)].append(hist_predict_CatBoost)

In [ ]:
for i in range(3):
  for b in backtesting_CatBoost[i]:
    h = bt_horizons[backtesting_CatBoost[i].index(b)]
    print_graph_backtesting(tests[i], b, True, 'CatBoost Model',h)

In [ ]:
add_row(['Backtesting Catboost Model','','','',''])
for i in range(3):
  add_row([f'time period = {i + 1}', '', '', '', ''])
  for b in backtesting_CatBoost[i]:
    print(f"MAE of CatBoost forecasting horizon = {bt_horizons[backtesting_CatBoost[i].index(b)]}: {mae(tests[i], b)}")
    print(f"RMSE of CatBoost forecasting horizon = {bt_horizons[backtesting_CatBoost[i].index(b)]}: {rmse(tests[i], b)}")
    print(f"MSE of CatBoost forecasting horizon = {bt_horizons[backtesting_CatBoost[i].index(b)]}: {mse(tests[i], b)}")
    print(f"MAPE of CatBoost forecasting horizon = {bt_horizons[backtesting_CatBoost[i].index(b)]}: {mape(tests[i], b)}")
    print("\n")
    row = [f'Catboost fh={bt_horizons[backtesting_CatBoost[i].index(b)]}', mae(tests[i], b), rmse(tests[i], b), mse(tests[i], b), mape(tests[i], b) ]
    add_row(row)